In [1]:
import blosc2
import numpy as np
import plotly.express as px
import ipywidgets as widgets
import plotly.graph_objects as go
import pandas as pd

In [2]:
path = '/home/blosc/gaia/gaia-3d-windows-int8-3.b2nd'
# path = '/Users/martaiborra/gaia_plots/gaia-3d-windows-int8-3.b2nd'

In [3]:
arr = blosc2.open(path)
arr.info

type    : NDArray
shape   : (20000, 20000, 20000)
chunks  : (250, 250, 250)
blocks  : (25, 25, 25)
dtype   : uint8
cratio  : 1140.70
cparams : {'blocksize': 15625,
 'clevel': 1,
 'codec': <Codec.ZSTD: 5>,
 'codec_meta': 0,
 'filters': [<Filter.NOFILTER: 0>,
             <Filter.NOFILTER: 0>,
             <Filter.NOFILTER: 0>,
             <Filter.NOFILTER: 0>,
             <Filter.NOFILTER: 0>,
             <Filter.SHUFFLE: 1>],
 'filters_meta': [0, 0, 0, 0, 0, 0],
 'nthreads': 16,
 'splitmode': <SplitMode.ALWAYS_SPLIT: 1>,
 'typesize': 1,
 'use_dict': 0}
dparams : {'nthreads': 16}

In [4]:
shape = arr.shape
# cube_shape = arr.chunks
# cube_shape = np.array([100, 100, 100])
cube_shape = np.array([50, 50, 50])


nsegments = 10

# global plot_output

plot_output = widgets.Output()


x_origin = widgets.IntText(
    min=0,
    max=shape[0] - cube_shape[0],
    step=1,
    description='X Origin:',
    value=0
)
y_origin = widgets.IntText(
    min=0,
    max=shape[1] - cube_shape[1],
    step=1,
    description='Y Origin:',
    value=0
)
z_origin = widgets.IntText(
    min=0,
    max=shape[2] - cube_shape[2],
    step=1,
    description='Z Origin:',
    value=0
)

In [5]:
axis_widget = widgets.Dropdown(
    options=[('x', 0), ('y', 1), ('z', 2)],
    value=0,
    description='Travel axis:',
    disabled=False,
)

In [6]:
def init(obj):
    global axis
    global step
    global start
    global nsteps
    global stop
    axis = axis_widget.value
    step = cube_shape[axis] // nsegments
    start = np.array([x_origin.value, y_origin.value, z_origin.value])
    global axis_origin
    axis_origin = start[axis]
    global nframes
    nframes = (shape[axis] - start[axis]) // step
    stop = start + np.array(cube_shape)
    # print("start ", start)
    # print("stop ", stop)

In [7]:
display(axis_widget)
coordinates_widgets = widgets.HBox(
[x_origin, y_origin, z_origin])
display(coordinates_widgets)

axis_widget.observe(init, names=['value'])
x_origin.observe(init, names=['value'])
y_origin.observe(init, names=['value'])
z_origin.observe(init, names=['value'])

a = 0
init(a)

Dropdown(description='Travel axis:', options=(('x', 0), ('y', 1), ('z', 2)), value=0)

In [22]:
# Animation using scatter
names = ["x", "y", "marker_size", "axis_start"]
print(nframes)
df = pd.DataFrame(columns=names)
i=0
red_axis = [1, 2, 0]
while stop[axis] < shape[axis]:
    npa = arr[start[0]:stop[0], start[1]:stop[1], start[2]:stop[2]]

    img = np.sum(npa, axis=axis)     
    idx = np.indices(img.shape)
    x = idx[0, :, :].flatten()
    y = idx[1, :, :].flatten()
    size = img.flatten()
    nstep = np.full(np.prod(img.shape), i)
    df_step = pd.DataFrame(x)
    df_step = pd.concat([df_step, pd.DataFrame(y)], axis=1)
    df_step = pd.concat([df_step, pd.DataFrame(size)], axis=1)
    df_step = pd.concat([df_step, pd.DataFrame(nstep)], axis=1)
    df_step.columns=names

    df = pd.concat([df, df_step], axis=0)
    
    
    start[axis] += step
    stop[axis] += step
    i+=1
    
print(df.size)
df.marker_size = df.marker_size.astype('int32')
df.dtypes
# Remove dots with no stars
df = df[~df['marker_size'].isin([0])]
df.reset_index(drop=True)
print(df.size)


df.head()

2400
23900000
222048


x   y  marker_size axis_start
107  2   7            1          0
159  3   9            1          0
163  3  13            1          0
229  4  29            1          0
254  5   4            1          0

In [23]:
fig = px.scatter(df, "x", "y", animation_frame='axis_start', opacity=0.8, size='marker_size',
                     color_discrete_sequence=['white']
                    )
# fig.update_traces(marker=dict(symbol="star"))
fig.update_layout(plot_bgcolor="black", paper_bgcolor='white')


fig.show()

In [14]:
l = np.array([1, 2, 3, 4]).reshape((2,2))
print(l)
print(np.sum(l, axis=0))
print(np.sum(l, axis=1))

[[1 2]
 [3 4]]
[4 6]
[3 7]
